In [1]:
import os
import sys
os.chdir("..")
# from matplotlib import pyplot as plt
# from matplotlib import patches
# from matplotlib import colors
import pandas as pd
import IPython.display as ipd
# import glob
import numpy as np
# import muspy
# import pypianoroll
import torch
from util.play_midi import play_midi
# !pip install miditok symusic
from miditok import REMI, TokenizerConfig
from miditok.pytorch_data import DataCollator, DatasetMIDI #, DatasetTok
from pathlib import Path
from symusic import Score
from torch.utils.data import DataLoader
os.getcwd()

'/home/youssef/Documents/project/lofi_radio'

In [2]:
config = TokenizerConfig()
tokenizer = REMI()
# midi_files = list(Path("/content/drive/MyDrive/uni/Project/code/audio/midi_songs").glob("**/*.mid"))
midi_files = list(Path("data/jazz_midi").glob("**/*.mid"))
print(f"number of midi_files = {len(midi_files)}")
print(f"number of vocab = {len(tokenizer.vocab)}")

number of midi_files = 934
number of vocab = 282


In [3]:
print(len(midi_files))
file_counter = len(midi_files)
corrupt_files = []
for file in midi_files: # removing corrupted files/ files that cant be fully understood
    try:
        Score(file)
    except:
        # corrupt_files.append(midi_files.pop(file))
        file_holder = file
        midi_files.remove(file)
        corrupt_files.append(file_holder)
print(len(midi_files))
for file in midi_files: # on windows this has to be run 2 times, i have no idea why.... very wierd
    try:
        Score(file)
    except:
        # corrupt_files.append(midi_files.pop(file))
        file_holder = file
        midi_files.remove(file)
        corrupt_files.append(file_holder)
print(len(midi_files))
print(f"corrupt file counter = {len(corrupt_files)} which is {'correct' if file_counter-len(midi_files)==len(corrupt_files) else 'incorrect'}")
file_counter = len(midi_files)

934
915
914
corrupt file counter = 20 which is correct


In [8]:
song = Score(midi_files[-18])
tokenized_song = tokenizer.midi_to_tokens(song)

song1 =tokenizer.tokens_to_midi(tokenized_song)
ids = tokenizer._tokens_to_ids(tokenized_song[-1])
len(tokenizer._ids_to_tokens(ids))
print(f"vocab size = {len(tokenizer)})

NameError: name 'printlen' is not defined

In [5]:
# tokenizer.learn_bpe(vocab_size=500, files_paths=midi_files)


In [5]:
from transformers import DataCollatorForLanguageModeling

max_seq_len = 256

dataset = DatasetMIDI( # seq_len = start + seq_len + end
    files_paths=midi_files,
    # min_seq_len=50, # 52
    max_seq_len=max_seq_len, # 514
    tokenizer=tokenizer,
    bos_token_id=tokenizer["BOS_None"],
    # eos_token_id=tokenizer["EOS_None"]
)

collator = DataCollator(
    pad_token_id=tokenizer["PAD_None"],
    copy_inputs_as_labels=True
)

data_collator = DataCollatorForLanguageModeling(tokenizer, mlm=False)

data_loader = DataLoader(dataset=dataset, batch_size=256, collate_fn=collator,)

In [7]:
# for batch in data_loader:
#     x, y, z = **batch
#     break
# y = **x
# y = tokenizer._ids_to_tokens(x["input_ids"][0].tolist())


In [19]:
from transformers import AutoConfig, GPT2LMHeadModel
from transformers.tokenization_utils_base import BatchEncoding


device = "cuda" if torch.cuda.is_available() else "cpu"
device 


'cpu'

In [7]:
context_length = 256
n_layer = 6
n_head = 8
n_emb = 256 # 512
# model = GPT2LMHeadModel.from_pretrained("openai-community/gpt2")
config = AutoConfig.from_pretrained(
    "gpt2",
    vocab_size=len(tokenizer),
    n_positions=context_length,
    n_layer=n_layer,
    n_head=n_head,
    pad_token_id=tokenizer["PAD_None"],
    bos_token_id=tokenizer["BOS_None"],
    eos_token_id=tokenizer["EOS_None"],
    n_embd=n_emb
)


In [8]:
model = GPT2LMHeadModel(config)
model_size = sum(t.numel() for t in model.parameters())
print(f"GPT-2 size: {model_size} parameters")
model

GPT-2 size: 4876800 parameters


GPT2LMHeadModel(
  (transformer): GPT2Model(
    (wte): Embedding(282, 256)
    (wpe): Embedding(256, 256)
    (drop): Dropout(p=0.1, inplace=False)
    (h): ModuleList(
      (0-5): 6 x GPT2Block(
        (ln_1): LayerNorm((256,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D()
          (c_proj): Conv1D()
          (attn_dropout): Dropout(p=0.1, inplace=False)
          (resid_dropout): Dropout(p=0.1, inplace=False)
        )
        (ln_2): LayerNorm((256,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D()
          (c_proj): Conv1D()
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.1, inplace=False)
        )
      )
    )
    (ln_f): LayerNorm((256,), eps=1e-05, elementwise_affine=True)
  )
  (lm_head): Linear(in_features=256, out_features=282, bias=False)
)

In [9]:
model.load_state_dict(torch.load("model/model_weights/remi_gpt2.pt"))

<All keys matched successfully>

In [20]:
model.eval()

with torch.no_grad():
    for batch in data_loader:
        full_inputs = BatchEncoding()
        full_inputs.update(batch)
        output_batch = batch
        labels = batch["labels"].to(device)
        outputs = model(**full_inputs)
        break
print(outputs["loss"])

tensor(3.4475)


In [12]:
# original song 
original_song = tokenizer._ids_to_tokens(output_batch["input_ids"][0].tolist())

midi_song_output = tokenizer.tokens_to_midi([original_song])
output_file_path = Path("data/output/", "output_input.mid")
midi_song_output.dump_midi(output_file_path)
play_midi(output_file_path)

In [17]:
len(outputs["logits"])

256

In [18]:
# song that is generated from original 
output_tokens = torch.tensor([[0]*len(outputs["logits"][0])]*len(outputs["logits"])) # [[0]*context_length]*batch_size
for i in range(len(outputs["logits"])):
    output_tokens[i] = torch.argmax(outputs["logits"][i], dim=-1)
tokens_output = tokenizer._ids_to_tokens(output_tokens[0].tolist())
midi_song_output = tokenizer.tokens_to_midi([tokens_output])
output_file_path = Path("data/output/", "decoded_midi.mid")
midi_song_output.dump_midi(output_file_path)
play_midi(output_file_path) 